In [1]:
import pandas as pd
import numpy as np

In [4]:
# Dataframe with Gvkey codes
codes = pd.read_csv('codes - Sheet2.csv')
codes.head()
len(codes) # Only has 496 companies

496

In [26]:
# Dataframe with CEO dismissal 
ceo = pd.read_csv('CEO_Dismissal_Database_9Nov23.csv')
ceo.head()
len(ceo['gvkey'].unique()) # Has 3677 companies
ceo.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8892 entries, 0 to 8891
Data columns (total 15 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   dismissal_dataset_id      8892 non-null   int64  
 1   coname                    8891 non-null   object 
 2   gvkey                     8892 non-null   int64  
 3   fyear                     8892 non-null   int64  
 4   co_per_rol                8892 non-null   int64  
 5   exec_fullname             8892 non-null   object 
 6   departure_code            8889 non-null   float64
 7   ceo_dismissal             8611 non-null   float64
 8   interim_coceo             560 non-null    object 
 9   tenure_no_ceodb           8892 non-null   int64  
 10  left_ceo_office           8607 non-null   object 
 11  date_departure_announced  1856 non-null   object 
 12  notes                     8831 non-null   object 
 13  sources                   8774 non-null   object 
 14  eight_ks

In [31]:
# Filter the dismissal data
ceo['date_departure_announced'] = ceo.apply(
    lambda row: row['left_ceo_office'] if pd.isna(row['date_departure_announced']) else row['date_departure_announced'],
    axis=1
)
ceo.info()
filtered_ceo = ceo.loc[ceo['departure_code'].isin([3, 4])].drop(columns=['fyear', 'co_per_rol', 'interim_coceo', 'tenure_no_ceodb', 'notes', 'sources', 'eight_ks', 'left_ceo_office']).reset_index(drop=True)
filtered_ceo.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8892 entries, 0 to 8891
Data columns (total 15 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   dismissal_dataset_id      8892 non-null   int64  
 1   coname                    8891 non-null   object 
 2   gvkey                     8892 non-null   int64  
 3   fyear                     8892 non-null   int64  
 4   co_per_rol                8892 non-null   int64  
 5   exec_fullname             8892 non-null   object 
 6   departure_code            8889 non-null   float64
 7   ceo_dismissal             8611 non-null   float64
 8   interim_coceo             560 non-null    object 
 9   tenure_no_ceodb           8892 non-null   int64  
 10  left_ceo_office           8607 non-null   object 
 11  date_departure_announced  8612 non-null   object 
 12  notes                     8831 non-null   object 
 13  sources                   8774 non-null   object 
 14  eight_ks

In [54]:
# Load and merge Gvkey df with dismissal df
gvkey = pd.read_csv('codes - Sheet2.csv')
dismissal_standardized = filtered_ceo.merge(gvkey,left_on="gvkey", right_on="Compustat gvkey", )
dismissal_standardized.dropna()
dismissal_standardized.info()
dismissal_standardized = dismissal_standardized[['dismissal_dataset_id','DTCC name', 'CRSP ticker','departure_code','ceo_dismissal','exec_fullname','date_departure_announced']]
dismissal_standardized['Fiscal Quarter'] = pd.to_datetime(dismissal_standardized['date_departure_announced']).dt.to_period('Q-DEC')
dismissal_standardized.head()


<class 'pandas.core.frame.DataFrame'>
Int64Index: 335 entries, 0 to 334
Data columns (total 17 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   dismissal_dataset_id      335 non-null    int64  
 1   coname                    335 non-null    object 
 2   gvkey                     335 non-null    int64  
 3   exec_fullname             335 non-null    object 
 4   departure_code            335 non-null    float64
 5   ceo_dismissal             335 non-null    float64
 6   date_departure_announced  335 non-null    object 
 7   Compustat gvkey           335 non-null    int64  
 8   Compustat name            335 non-null    object 
 9   Mergent FISD name         335 non-null    object 
 10  Mergent FISD issuer_id    335 non-null    int64  
 11  CRSP ticker               333 non-null    object 
 12  CRSP equity cusip         335 non-null    object 
 13  CRSP permno               335 non-null    int64  
 14  CRSP permc

dismissal_dataset_id                         DTCC name CRSP ticker  \
0                    44      ADVANCED MICRO DEVICES, INC.         AMD   
1                    45      ADVANCED MICRO DEVICES, INC.         AMD   
2                    52                        AETNA INC.         AET   
3                    67  AIR PRODUCTS AND CHEMICALS, INC.         APD   
4                    84       IKON OFFICE SOLUTIONS, INC.         IKN   

   departure_code  ceo_dismissal                exec_fullname  \
0             3.0            1.0  Hector de Jesus Ruiz, Ph.D.   
1             3.0            1.0             Derrick R. Meyer   
2             3.0            1.0             Richard L. Huber   
3             3.0            1.0              John E. McGlade   
4             3.0            1.0                 Ray B. Mundt   

  date_departure_announced Fiscal Quarter  
0                7/17/2008         2008Q3  
1                1/10/2011         2011Q1  
2                2/25/2000         2000Q1  
3                9/26/2013         2013Q3  
4                7/31/1993         1993Q3

In [55]:
!pip install ratelimit

In [57]:
# Retrive company's financial data from datajockey using API key and ratelimit to make multiple subsequent calls to build Panel data
import requests
import json
from tqdm import tqdm
from ratelimit import limits, sleep_and_retry

@sleep_and_retry
@limits(calls=10, period=60)
def call_api(symbol):
    response = requests.get(f"https://api.datajockey.io/v0/company/financials?apikey=837a05cca328ffa0890170f4daddb4f267ce37c2aa6f6a13e000&ticker={symbol}&period=Q&filetype=json")

    if response.status_code != 200:
        raise Exception('API response: {} and {}'.format(response.status_code, response.json()))
    return response.json()


def build_fundamentals_data(df):
  results = []
  exception_statements = []
  for symbol in tqdm(df):
      try:
          result = call_api(symbol)
          results.append(result)
      except Exception as e:
          exception_statements.append(f"Failed for symbol {symbol} with message: {str(e)}")

  for statement in exception_statements:
      print(statement)

  with open('fundamentals_results.json', 'w') as output_file:
        json.dump(results, output_file)
        
        
build_fundamentals_data(dismissal_standardized['CRSP ticker'].unique())

100%|██████████| 219/219 [21:05<00:00,  5.78s/it]


In [58]:
with open('fundamentals_results.json') as f:
    financials = json.load(f)
    
financials

[{'currency': 'USD',
  'company_info': {'cik': '2488',
   'ticker': 'AMD',
   'name': 'ADVANCED MICRO DEVICES, INC'},
  'financial_data': {'quarterly': {'revenue': {'2009Q2': 1184000000,
     '2009Q3': 1396000000,
     '2010Q1': 1574000000,
     '2010Q2': 1653000000,
     '2010Q3': 1618000000,
     '2010Q4': 1649000000,
     '2011Q1': 1613000000,
     '2011Q2': 1574000000,
     '2011Q3': 1690000000,
     '2011Q4': 1691000000,
     '2012Q1': 1585000000,
     '2012Q2': 1413000000,
     '2012Q3': 1269000000,
     '2012Q4': 1155000000,
     '2013Q1': 1088000000,
     '2013Q2': 1161000000,
     '2013Q3': 1461000000,
     '2013Q4': 1589000000,
     '2014Q1': 1397000000,
     '2014Q2': 1441000000,
     '2014Q3': 1429000000,
     '2014Q4': 1239000000,
     '2015Q1': 1030000000,
     '2015Q2': 942000000,
     '2015Q3': 1061000000,
     '2015Q4': 958000000,
     '2016Q1': 832000000,
     '2016Q2': 1027000000,
     '2016Q3': 1307000000,
     '2016Q4': 1153000000,
     '2017Q1': 1178000000,
     '

In [60]:
from tqdm import tqdm

record_set = ["net_income", "operating_income", 'eps_diluted', 'eps_basic']
df = pd.DataFrame(columns=["ticker", "quarter", *record_set])

for record in tqdm(financials):
    start_quarter, end_quarter = None, None
    try: 
        for variable in record_set:
            record_keys = list(record["financial_data"]["quarterly"][variable].keys())

            if len(record_keys) != 0:
                smallest_quarter_in_record = min(record_keys)
                biggest_quarter_in_record = max(record_keys)
                start_quarter = min(start_quarter, smallest_quarter_in_record) if start_quarter is not None else smallest_quarter_in_record
                end_quarter = max(end_quarter, biggest_quarter_in_record) if end_quarter is not None else biggest_quarter_in_record

        quarter_list = [start_quarter]
        start_quarter = [int(entry) for entry in start_quarter.split("Q")]
        running_quarter = start_quarter
        pres_quarter = None
        while pres_quarter != end_quarter:
            running_quarter[0] = running_quarter[0] + (running_quarter[1])//4
            running_quarter[1] = running_quarter[1]%4 + 1
            pres_quarter = f"{running_quarter[0]}Q{running_quarter[1]}"
            quarter_list.append(pres_quarter)

        for quarter in quarter_list:
            revenue = record["financial_data"]["quarterly"]["revenue"].get(quarter, None)
            operating_income = record["financial_data"]["quarterly"]["operating_income"].get(quarter, None)
            net_profit = record["financial_data"]["quarterly"]["net_income"].get(quarter, None)
            operating_margin = operating_income/revenue if operating_income != None and revenue != None and revenue != 0 else None
            net_profit_margin = net_profit/revenue if net_profit != None and revenue != None and revenue != 0 else None
            eps_diluted = record["financial_data"]["quarterly"]["eps_diluted"].get(quarter, None)
            eps_basic = record["financial_data"]["quarterly"]["eps_basic"].get(quarter, None)
            df.loc[len(df.index)] = [record['company_info']['ticker'], quarter, operating_margin, net_profit_margin, eps_diluted, eps_basic]
    except:
        continue
df["quarter"] = pd.to_datetime(df["quarter"]).dt.to_period('Q-DEC')
df

  0%|          | 0/219 [00:00<?, ?it/s]

100%|██████████| 219/219 [05:15<00:00,  1.44s/it]


ticker quarter net_income operating_income eps_diluted eps_basic
0       AMD  2009Q2  -0.210304        -0.282939        -0.5      -0.5
1       AMD  2009Q3  -0.055158        -0.096705       -0.19     -0.19
2       AMD  2009Q4        NaN              NaN         NaN       NaN
3       AMD  2010Q1   0.115629         0.163278        0.34      0.36
4       AMD  2010Q2    0.07562        -0.026013       -0.06     -0.06
...     ...     ...        ...              ...         ...       ...
8424     BG  2022Q3   0.029596         0.022674        2.49      2.52
8425     BG  2022Q4   0.030312         0.020168        2.19      2.26
8426     BG  2023Q1   0.054932         0.041232        4.15      4.21
8427     BG  2023Q2   0.054954         0.041332        4.09      4.13
8428     BG  2023Q3   0.035355         0.026218        2.47       2.5

[8429 rows x 6 columns]

In [87]:
# Sort fundamentals data by ticker and quarter in an ascending order 
df_sorted = df.sort_values(by=['ticker','quarter'],ascending=True)
df_sorted.reset_index(drop=True, inplace=True)
df_sorted.head(10)
df_sorted.info()
dismissal_standardized.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8429 entries, 0 to 8428
Data columns (total 6 columns):
 #   Column            Non-Null Count  Dtype        
---  ------            --------------  -----        
 0   ticker            8429 non-null   object       
 1   quarter           8429 non-null   period[Q-DEC]
 2   net_income        7326 non-null   object       
 3   operating_income  7564 non-null   object       
 4   eps_diluted       7737 non-null   object       
 5   eps_basic         7577 non-null   object       
dtypes: object(5), period[Q-DEC](1)
memory usage: 395.2+ KB
<class 'pandas.core.frame.DataFrame'>
Int64Index: 335 entries, 0 to 334
Data columns (total 8 columns):
 #   Column                    Non-Null Count  Dtype        
---  ------                    --------------  -----        
 0   dismissal_dataset_id      335 non-null    int64        
 1   DTCC name                 238 non-null    object       
 2   CRSP ticker               333 non-null    object       
 

In [167]:
# Merge Dismissals with company's Fundamental Financial data
dismissal_and_financials = df.merge(dismissal_standardized, left_on = ["ticker", "quarter"], right_on=["CRSP ticker", "Fiscal Quarter"], how = "left")[["ticker", "quarter", "net_income", "operating_income", "eps_diluted", "eps_basic", "dismissal_dataset_id"]]
dismissal_and_financials = dismissal_and_financials.rename(columns={"dismissal_dataset_id": "CEO_Dismissed", "net_income": "Net_Income", "operating_income": "Operating_Income"})
dismissal_and_financials['CEO_Dismissed'] = dismissal_and_financials['CEO_Dismissed'].apply(lambda x: 0 if pd.isnull(x) else 1)
dismissal_and_financials.rename(columns={'ticker':'Symbol'})
dismissal_and_financials.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 8429 entries, 0 to 8428
Data columns (total 7 columns):
 #   Column            Non-Null Count  Dtype        
---  ------            --------------  -----        
 0   ticker            8429 non-null   object       
 1   quarter           8429 non-null   period[Q-DEC]
 2   Net_Income        7326 non-null   object       
 3   Operating_Income  7564 non-null   object       
 4   eps_diluted       7737 non-null   object       
 5   eps_basic         7577 non-null   object       
 6   CEO_Dismissed     8429 non-null   int64        
dtypes: int64(1), object(5), period[Q-DEC](1)
memory usage: 526.8+ KB


In [98]:
dismissal_and_financials.to_csv('dismissal_and_financials.csv', index=False) 

In [102]:
!pip install xlrd

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 96.5/96.5 kB 819.2 kB/s eta 0:00:00 0:00:01


In [187]:
# Set up quarterly Adjusted Close data
quarterly_adjusted_close = pd.read_csv('adjusted_close_with_sector.csv')
quarterly_adjusted_close['Quarter'] = pd.to_datetime(quarterly_adjusted_close['quarter']).dt.to_period('Q-DEC')
quarterly_adjusted_close = quarterly_adjusted_close[quarterly_adjusted_close['Quarter'] >= pd.Period('2008Q1')]
quarterly_adjusted_close.reset_index(drop=True,inplace=True)
quarterly_adjusted_close

Symbol     quarter  Adjusted Close  GICS Sector  \
0          A  2008-03-31       19.208344  Health Care   
1          A  2008-06-30       22.885160  Health Care   
2          A  2008-09-30       19.098869  Health Care   
3          A  2008-12-31       10.064579  Health Care   
4          A  2009-03-31        9.897156  Health Care   
...      ...         ...             ...          ...   
32187    ZTS  2022-12-31      144.896637  Health Care   
32188    ZTS  2023-03-31      164.948898  Health Care   
32189    ZTS  2023-06-30      171.033752  Health Care   
32190    ZTS  2023-09-30      173.171677  Health Care   
32191    ZTS  2023-12-31      196.923355  Health Care   

                    GICS Sub-Industry  Date added Quarter  
0      Life Sciences Tools & Services  2000-06-05  2008Q1  
1      Life Sciences Tools & Services  2000-06-05  2008Q2  
2      Life Sciences Tools & Services  2000-06-05  2008Q3  
3      Life Sciences Tools & Services  2000-06-05  2008Q4  
4      Life Sciences Tools & Services  2000-06-05  2009Q1  
...                               ...         ...     ...  
32187                 Pharmaceuticals  2013-06-21  2022Q4  
32188                 Pharmaceuticals  2013-06-21  2023Q1  
32189                 Pharmaceuticals  2013-06-21  2023Q2  
32190                 Pharmaceuticals  2013-06-21  2023Q3  
32191                 Pharmaceuticals  2013-06-21  2023Q4  

[32192 rows x 7 columns]

In [168]:
# Set up treasury yield dataframe
treasury_yield = pd.read_excel('allmonth.xls')
treasury_yield['Quarter'] = pd.to_datetime(treasury_yield['Date']).dt.to_period('Q-DEC')
treasury_yield = treasury_yield[treasury_yield['Quarter'] >= pd.Period('2008Q1')]
treasury_yield.reset_index(drop=True, inplace=True)
# treasury_yield
# Calculate moving average for each column
treasury_yield_quarterly = treasury_yield.groupby('Quarter').mean()
treasury_yield_quarterly = treasury_yield_quarterly.reset_index()
treasury_yield_quarterly.rename(columns={'Quarter':'Fiscal Quarter'}, inplace=True)
treasury_yield_quarterly.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 69 entries, 0 to 68
Data columns (total 7 columns):
 #   Column                                          Non-Null Count  Dtype        
---  ------                                          --------------  -----        
 0   Fiscal Quarter                                  69 non-null     period[Q-DEC]
 1   10 Year Treasury Yield                          65 non-null     float64      
 2   3 Month Treasury Yield                          65 non-null     float64      
 3   3 Month Treasury Yield (Bond Equivalent Basis)  65 non-null     float64      
 4   Spread                                          65 non-null     float64      
 5   Rec_prob                                        69 non-null     float64      
 6   NBER_Rec                                        65 non-null     float64      
dtypes: float64(6), period[Q-DEC](1)
memory usage: 3.9 KB


/var/folders/ws/y4s13dw95dd92p32p0mgjt600000gn/T/ipykernel_12204/2781219537.py:8: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  treasury_yield_quarterly = treasury_yield.groupby('Quarter').mean()


In [196]:
# Merging with treasury yield data
fin_and_interest_merged = dismissal_and_financials.merge(treasury_yield_quarterly, left_on='quarter', right_on='Fiscal Quarter', how='left')
fin_and_interest_merged = fin_and_interest_merged.drop(columns={'Fiscal Quarter'})
fin_and_interest_merged

ticker quarter Net_Income Operating_Income eps_diluted eps_basic  \
0       AMD  2009Q2  -0.210304        -0.282939        -0.5      -0.5   
1       AMD  2009Q3  -0.055158        -0.096705       -0.19     -0.19   
2       AMD  2009Q4        NaN              NaN         NaN       NaN   
3       AMD  2010Q1   0.115629         0.163278        0.34      0.36   
4       AMD  2010Q2    0.07562        -0.026013       -0.06     -0.06   
...     ...     ...        ...              ...         ...       ...   
8424     BG  2022Q3   0.029596         0.022674        2.49      2.52   
8425     BG  2022Q4   0.030312         0.020168        2.19      2.26   
8426     BG  2023Q1   0.054932         0.041232        4.15      4.21   
8427     BG  2023Q2   0.054954         0.041332        4.09      4.13   
8428     BG  2023Q3   0.035355         0.026218        2.47       2.5   

      CEO_Dismissed  10 Year Treasury Yield  3 Month Treasury Yield  \
0                 0                3.313333                0.173333   
1                 0                3.516667                0.156667   
2                 0                3.460000                0.056667   
3                 0                3.716667                0.106667   
4                 0                3.490000                0.146667   
...             ...                     ...                     ...   
8424              0                3.106667                2.663333   
8425              0                3.830000                4.040000   
8426              0                3.646667                4.626667   
8427              0                3.593333                5.073333   
8428              0                4.150000                5.290000   

      3 Month Treasury Yield (Bond Equivalent Basis)    Spread  Rec_prob  \
0                                           0.175818  3.137515  0.026125   
1                                           0.158907  3.357759  0.022440   
2                                           0.057462  3.402538  0.010140   
3                                           0.108181  3.608486  0.016806   
4                                           0.148760  3.341240  0.006712   
...                                              ...       ...       ...   
8424                                        2.718981  0.387685  0.090031   
8425                                        4.138513 -0.308513  0.070651   
8426                                        4.746447 -1.099780  0.058926   
8427                                        5.210650 -1.617317  0.045808   
8428                                        5.436167 -1.286167  0.219478   

      NBER_Rec  
0          1.0  
1          0.0  
2          0.0  
3          0.0  
4          0.0  
...        ...  
8424       0.0  
8425       0.0  
8426       0.0  
8427       0.0  
8428       0.0  

[8429 rows x 13 columns]

In [207]:
# Polishing the final dataset
final_dataset_publish = fin_and_interest_merged.merge(quarterly_adjusted_close, left_on=['ticker','quarter'], right_on=['Symbol','Quarter'], how='left')
final_dataset_publish = final_dataset_publish.drop(columns={'Symbol','quarter_y','Quarter'})
final_dataset_publish = final_dataset_publish.rename(columns={'quarter_x':'Fiscal Quarter','ticker':'CRSP Ticker','Net_Income':'Net Income','Operating_Income':'Operating Income','eps_diluted':'EPS Diluted','eps_basic':'EPS Basic','CEO_Dismissed':'CEO Dismissal','adjusted_close':'Adjusted Close Price','Rec_prob':'Recession Probability','NBER_Rec':'Recession'})
final_dataset = final_dataset_publish.sort_values(by=['CRSP Ticker','Fiscal Quarter'],ascending=True)
final_dataset_publish = final_dataset_publish.dropna()
count_1 = final_dataset_publish['CEO Dismissal'].sum()
count_1

64

In [208]:
# Add condition to set CEO Dismissal = 1 for previous two quarters if CEO Dismissal = 1 for a given company in a given quarter
final_dataset_publish['CEO Dismissal'] = final_dataset_publish.groupby('CRSP Ticker')['CEO Dismissal'].apply(lambda x: x.rolling(3).max().fillna(x))
# Check if the condition was applied correctly
count_2 = final_dataset_publish['CEO Dismissal'].sum()
count_2

/var/folders/ws/y4s13dw95dd92p32p0mgjt600000gn/T/ipykernel_12204/1228871397.py:2: FutureWarning: Not prepending group keys to the result index of transform-like apply. In the future, the group keys will be included in the index, regardless of whether the applied function returns a like-indexed object.
To preserve the previous behavior, use

	>>> .groupby(..., group_keys=False)

To adopt the future behavior and silence this warning, use 

	>>> .groupby(..., group_keys=True)
  final_dataset_publish['CEO Dismissal'] = final_dataset_publish.groupby('CRSP Ticker')['CEO Dismissal'].apply(lambda x: x.rolling(3).max().fillna(x))


190.0

In [212]:
# Save the dataset
final_dataset_publish.to_csv('final_dataset_mine.csv',index=False)


In [210]:
final_dataset_publish.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4332 entries, 0 to 8428
Data columns (total 17 columns):
 #   Column                                          Non-Null Count  Dtype        
---  ------                                          --------------  -----        
 0   CRSP Ticker                                     4332 non-null   object       
 1   Fiscal Quarter                                  4332 non-null   period[Q-DEC]
 2   Net Income                                      4332 non-null   object       
 3   Operating Income                                4332 non-null   object       
 4   EPS Diluted                                     4332 non-null   object       
 5   EPS Basic                                       4332 non-null   object       
 6   CEO Dismissal                                   4332 non-null   float64      
 7   10 Year Treasury Yield                          4332 non-null   float64      
 8   3 Month Treasury Yield                          4332 non-n